In [40]:
import numpy as np
import msicpe.san as san
from plotly import express as px
import scipy.signal as signal

# Partie 1 - Introduction à l’analyse spectrale

In [41]:
signal_dict1 = np.load('generator.npz') # signal_dict est un dictionnaire contenant les données contenues dans le fichier signal.npz
s = signal_dict1['s'] # extraction du signal utile
t = signal_dict1['t'] # extraction du vecteur temps associé au signal

nu1, sF1 = san.trans_fourier(s, t)

spectre1 = np.abs(sF1)

px.line(x = t, y = s, labels={"x":"Temps", "y":"Amplitude"}, title="generator.npz").show()
px.line(x = nu1, y = spectre1, labels={"x":"Fréquence", "y":"Amplitude"}, title="spectre generator.npz").show()

In [42]:
signal_dict1 = np.load('piano_G.npz') # signal_dict est un dictionnaire contenant les données contenues dans le fichier signal.npz
s = signal_dict1['s'] # extraction du signal utile
t = signal_dict1['t'] # extraction du vecteur temps associé au signal

nu2, sF2 = san.trans_fourier(s, t)

spectre2 = np.abs(sF2)

px.line(x = t, y = s, labels={"x":"Temps", "y":"Amplitude"}, title="piano_G.npz").show()
px.line(x = nu2, y = spectre2, labels={"x":"Fréquence", "y":"Amplitude"}, title="spectre piano_G.npz").show()

In [43]:
signal_dict1 = np.load('noise.npz') # signal_dict est un dictionnaire contenant les données contenues dans le fichier signal.npz
s = signal_dict1['s'] # extraction du signal utile
t = signal_dict1['t'] # extraction du vecteur temps associé au signal

nu3, sF3 = san.trans_fourier(s, t)

spectre3 = np.abs(sF3)

px.line(x = t, y = s, labels={"x":"Temps", "y":"Amplitude"}, title="noise.npz").show()
px.line(x = nu3, y = spectre3, labels={"x":"Fréquence", "y":"Amplitude"}, title="spectre noise.npz").show()

In [59]:
signal_dict1 = np.load('ecg_signal.npz') # signal_dict est un dictionnaire contenant les données contenues dans le fichier signal.npz
s = signal_dict1['s'] # extraction du signal utile
t = signal_dict1['t'] # extraction du vecteur temps associé au signal

nu4, sF4 = san.trans_fourier(s - np.mean(s), t)

spectre4 = np.abs(sF4)

px.line(x = t, y = s, labels={"x":"Temps", "y":"Amplitude"}, title="ecg_signal.npz").show()
px.line(x = nu4, y = spectre4, labels={"x":"Fréquence", "y":"Amplitude"}, title="spectre ecg_signal.npz").show()

# Partie 2 - Reconnaissance automatique de voyelle

### 2.1 Lecture des fichiers et affichages

In [94]:
dat = np.load('apprentissage/a_1.npz') # dat est un dictionnaire contenant les données contenues dans le fichier .npz
s = dat['s'] # extraction du signal utile
t = dat['t'] # extraction du vecteur temps associé au signal

nu, tf_s = san.trans_fourier(s, t)

px.line(x = t, y = s, labels={"x":"Temps", "y":"Amplitude"}, title="Signal temporel a_1").show()


In [81]:
px.line(x = nu, y = abs(tf_s), labels={"x":"Fréquence", "y":"Amplitude"}, title="Spectre du signal a_1").show()

Les différents pics correspondent aux harmoniques du signal a_1

In [80]:
px.line(x = nu, y = np.log10(abs(tf_s)), labels={"x":"Fréquence", "y":"Amplitude en log base 10"}, title="Log(base 10) du spectre du signal a_1").show()

Le fait d'appliquer le log base 10 permet de mettre en évidence les harmoniques qui étaient très peu visibles car elles avaient une amplitude trop faible comparée aux autres qui dominaient

### 2.2 Apprentissage − Caractérisation des voyelles

In [ ]:
H = 12 # Nombre d'harmoniques

# Fonction qui crée le vecteur cherché
def vecteur(nom_fichier):
    dat = np.load(nom_fichier)
    s = dat['s']
    t = dat['t']

    nu1, tf_s = san.trans_fourier(s, t)
    spectre = np.abs(tf_s)
    spectre_normalise = spectre / np.max(spectre)
    f0 = san.detect_fondamentale(spectre_normalise, nu)
    V, A = san.detect_pics(np.log10(spectre_normalise), [k * f0 for k in range (1, H+1)], nu)

    return [san.detect_fondamentale(spectre_normalise, nu)] , A

# Création des vecteurs
VA1 = vecteur('apprentissage/a_1.npz')
VA2 = vecteur('apprentissage/a_2.npz')
VA3 = vecteur('apprentissage/a_3.npz')
VA4 = vecteur('apprentissage/a_4.npz')
VA5 = vecteur('apprentissage/a_5.npz')

# IL FAUT QU'ON FASSE LE SIGNAL 5

print(VA1, VA2, VA3, VA4, VA5)

([np.float64(106.96433630555556)], array([-0.01770413, -0.11153866, -0.67250025, -0.6368319 , -0.82254314,
       -0.7623576 , -0.43994352, -0.20462221, -0.5069877 , -1.1035581 ,
       -0.6151614 , -0.4991833 ], dtype=float32)) ([np.float64(113.96200316666666)], array([ 0.        , -0.10836832, -0.6702799 , -0.39504966, -0.70660025,
       -0.23800159, -0.28642192, -0.53606224, -0.8869372 , -0.7948717 ,
       -0.44360533, -0.96382415], dtype=float32)) ([np.float64(0.0)], array([-1.0133272, -1.0133272, -1.0133272, -1.0133272, -1.0133272,
       -1.0133272, -1.0133272, -1.0133272, -1.0133272, -1.0133272,
       -1.0133272, -1.0133272], dtype=float32)) ([np.float64(110.96300308333333)], array([ 0.        , -0.07872204, -0.9172031 , -0.8323034 , -1.1711625 ,
       -0.43714795, -0.4251856 , -0.36361626, -0.72709036, -0.48628333,
       -0.5399125 , -0.7437523 ], dtype=float32)) ([np.float64(0.0)], array([-1.3584889, -1.3584889, -1.3584889, -1.3584889, -1.3584889,
       -1.3584889, -1.35